<a href="https://colab.research.google.com/github/amandaliusa/cs155-kaggle/blob/master/catboost.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import AdaBoostClassifier
from sklearn.metrics import roc_curve, auc

In [2]:
import tensorflow as tf
from tensorflow.python.data import Dataset
import keras
from keras.utils import to_categorical
from keras import models
from keras import layers

Using TensorFlow backend.


In [3]:
import io
df_train = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')

In [4]:
# replace missing values with median (less sensitive to outliers)
df_train['opened_position_qty '].fillna(df_train['opened_position_qty '].median(),inplace=True)
df_test['opened_position_qty '].fillna(df_train['opened_position_qty '].median(),inplace=True)
df_train['closed_position_qty'].fillna(df_train['closed_position_qty'].median(),inplace=True)
df_test['closed_position_qty'].fillna(df_train['closed_position_qty'].median(), inplace=True)

In [5]:
df = pd.concat([df_train,df_test],sort=False)

In [6]:
# engineer new features by grouping like features 
bid_cols = ['bid1','bid2', 'bid3', 'bid4', 'bid5']
bid_vol_cols = ['bid1vol', 'bid2vol', 'bid3vol', 'bid4vol', 'bid5vol']
ask_cols = ['ask1', 'ask2', 'ask3', 'ask4', 'ask5',]
ask_vol_cols = ['ask1vol','ask2vol', 'ask3vol', 'ask4vol', 'ask5vol']
group_cols = {"bid_cols":bid_cols,"bid_vol_cols":bid_vol_cols,"ask_cols":ask_cols,"ask_vol_cols":ask_vol_cols}

In [7]:
for group in group_cols.keys():
    print(group)
    df[f"{group}_max"] = df[group_cols[group]].max(axis=1)
    df[f"{group}_min"] = df[group_cols[group]].min(axis=1)
    df[f"{group}_spread"] = df[f"{group}_max"].div(df[f"{group}_min"])
    #df[f"{group}_logsumexp"] = df[group_cols[group]].apply(logsumexp)
    
    df[f"{group}_max"] = df[group_cols[group]].max(axis=1)
    
df["last_price_div__mid"] = df["last_price"].div(df["mid"])

bid_cols
bid_vol_cols
ask_cols
ask_vol_cols


In [8]:
x_train = df.loc[~df.y.isna()]
y_train = x_train['y']
x_train = x_train.drop(['y'], axis=1)
x_test = df.loc[df.y.isna()]
x_test = x_test.drop(['y'], axis=1)

In [9]:
# Normalize data
from sklearn import preprocessing

x_train = df_train[df_train.columns[1:27]]
y_train = df_train['y']
x_test = df_test[df_test.columns[1:]]

# Normalize training data by subtracting mean and scaling to unit variance
std_scale = preprocessing.StandardScaler().fit(x_train)
x_train_norm = std_scale.transform(x_train)
x_train = pd.DataFrame(x_train_norm, index=x_train.index, columns=x_train.columns)

# Normalize testing data by using mean and SD of training set
x_test_norm = std_scale.transform(x_test)
x_test = pd.DataFrame(x_test_norm, index=x_test.index, columns=x_test.columns) 

In [10]:
# Split training and validation data 
from sklearn.model_selection import train_test_split
x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.2)

In [16]:
import catboost
from catboost import Pool, CatBoostClassifier
model = CatBoostClassifier(
    iterations=20000,
    learning_rate=0.01,
    task_type='GPU',
)
  
model.fit(
      x_train, y_train,
      eval_set=(x_val, y_val),
      verbose=10,
)  

print(model.get_best_score())


0:	learn: 0.6916990	test: 0.6917124	best: 0.6917124 (0)	total: 32.3ms	remaining: 10m 46s
10:	learn: 0.6787869	test: 0.6789292	best: 0.6789292 (10)	total: 354ms	remaining: 10m 42s
20:	learn: 0.6683336	test: 0.6685975	best: 0.6685975 (20)	total: 680ms	remaining: 10m 46s
30:	learn: 0.6598990	test: 0.6602926	best: 0.6602926 (30)	total: 1s	remaining: 10m 46s
40:	learn: 0.6529887	test: 0.6535155	best: 0.6535155 (40)	total: 1.33s	remaining: 10m 48s
50:	learn: 0.6473540	test: 0.6479987	best: 0.6479987 (50)	total: 1.67s	remaining: 10m 53s
60:	learn: 0.6427710	test: 0.6435337	best: 0.6435337 (60)	total: 2.01s	remaining: 10m 55s
70:	learn: 0.6390233	test: 0.6399167	best: 0.6399167 (70)	total: 2.34s	remaining: 10m 55s
80:	learn: 0.6359466	test: 0.6369731	best: 0.6369731 (80)	total: 2.66s	remaining: 10m 53s
90:	learn: 0.6334230	test: 0.6345725	best: 0.6345725 (90)	total: 2.98s	remaining: 10m 51s
100:	learn: 0.6313233	test: 0.6325909	best: 0.6325909 (100)	total: 3.3s	remaining: 10m 49s
110:	learn: 0

900:	learn: 0.6125262	test: 0.6222851	best: 0.6222851 (900)	total: 34.4s	remaining: 12m 8s
910:	learn: 0.6124448	test: 0.6222767	best: 0.6222767 (910)	total: 34.7s	remaining: 12m 6s
920:	learn: 0.6123527	test: 0.6222640	best: 0.6222640 (920)	total: 35s	remaining: 12m 5s
930:	learn: 0.6122597	test: 0.6222514	best: 0.6222511 (929)	total: 35.3s	remaining: 12m 3s
940:	learn: 0.6121806	test: 0.6222396	best: 0.6222396 (940)	total: 35.7s	remaining: 12m 2s
950:	learn: 0.6121101	test: 0.6222297	best: 0.6222297 (950)	total: 36s	remaining: 12m
960:	learn: 0.6120303	test: 0.6222190	best: 0.6222190 (960)	total: 36.3s	remaining: 11m 58s
970:	learn: 0.6119499	test: 0.6222105	best: 0.6222105 (970)	total: 36.6s	remaining: 11m 56s
980:	learn: 0.6118711	test: 0.6222021	best: 0.6222021 (980)	total: 36.9s	remaining: 11m 55s
990:	learn: 0.6117889	test: 0.6221928	best: 0.6221928 (990)	total: 37.2s	remaining: 11m 54s
1000:	learn: 0.6116866	test: 0.6221828	best: 0.6221828 (1000)	total: 37.5s	remaining: 11m 52s

1780:	learn: 0.6048544	test: 0.6213890	best: 0.6213882 (1778)	total: 1m 13s	remaining: 12m 34s
1790:	learn: 0.6047720	test: 0.6213729	best: 0.6213729 (1790)	total: 1m 14s	remaining: 12m 35s
1800:	learn: 0.6046836	test: 0.6213669	best: 0.6213667 (1799)	total: 1m 14s	remaining: 12m 37s
1810:	learn: 0.6046004	test: 0.6213586	best: 0.6213582 (1809)	total: 1m 15s	remaining: 12m 38s
1820:	learn: 0.6045199	test: 0.6213502	best: 0.6213498 (1819)	total: 1m 16s	remaining: 12m 40s
1830:	learn: 0.6044413	test: 0.6213415	best: 0.6213408 (1829)	total: 1m 16s	remaining: 12m 41s
1840:	learn: 0.6043449	test: 0.6213357	best: 0.6213357 (1840)	total: 1m 17s	remaining: 12m 42s
1850:	learn: 0.6042546	test: 0.6213228	best: 0.6213228 (1850)	total: 1m 17s	remaining: 12m 44s
1860:	learn: 0.6041632	test: 0.6213159	best: 0.6213159 (1860)	total: 1m 18s	remaining: 12m 46s
1870:	learn: 0.6040692	test: 0.6213073	best: 0.6213073 (1870)	total: 1m 19s	remaining: 12m 47s
1880:	learn: 0.6039767	test: 0.6212989	best: 0.621

2650:	learn: 0.5973271	test: 0.6206361	best: 0.6206361 (2650)	total: 2m 6s	remaining: 13m 45s
2660:	learn: 0.5972309	test: 0.6206260	best: 0.6206260 (2659)	total: 2m 6s	remaining: 13m 46s
2670:	learn: 0.5971647	test: 0.6206234	best: 0.6206234 (2670)	total: 2m 7s	remaining: 13m 47s
2680:	learn: 0.5970710	test: 0.6206188	best: 0.6206188 (2680)	total: 2m 8s	remaining: 13m 47s
2690:	learn: 0.5969832	test: 0.6206055	best: 0.6206055 (2690)	total: 2m 8s	remaining: 13m 48s
2700:	learn: 0.5968919	test: 0.6205958	best: 0.6205958 (2700)	total: 2m 9s	remaining: 13m 49s
2710:	learn: 0.5967873	test: 0.6205864	best: 0.6205864 (2710)	total: 2m 10s	remaining: 13m 49s
2720:	learn: 0.5966903	test: 0.6205814	best: 0.6205814 (2720)	total: 2m 10s	remaining: 13m 49s
2730:	learn: 0.5966154	test: 0.6205673	best: 0.6205673 (2730)	total: 2m 11s	remaining: 13m 49s
2740:	learn: 0.5965345	test: 0.6205578	best: 0.6205578 (2740)	total: 2m 11s	remaining: 13m 50s
2750:	learn: 0.5964652	test: 0.6205500	best: 0.6205500 (

3520:	learn: 0.5898405	test: 0.6200080	best: 0.6200080 (3520)	total: 2m 58s	remaining: 13m 53s
3530:	learn: 0.5897607	test: 0.6199995	best: 0.6199995 (3530)	total: 2m 58s	remaining: 13m 53s
3540:	learn: 0.5896674	test: 0.6199910	best: 0.6199910 (3540)	total: 2m 59s	remaining: 13m 52s
3550:	learn: 0.5895826	test: 0.6199822	best: 0.6199822 (3550)	total: 2m 59s	remaining: 13m 52s
3560:	learn: 0.5895034	test: 0.6199742	best: 0.6199742 (3560)	total: 3m	remaining: 13m 52s
3570:	learn: 0.5894178	test: 0.6199706	best: 0.6199706 (3570)	total: 3m	remaining: 13m 52s
3580:	learn: 0.5893357	test: 0.6199599	best: 0.6199599 (3580)	total: 3m 1s	remaining: 13m 52s
3590:	learn: 0.5892401	test: 0.6199514	best: 0.6199514 (3590)	total: 3m 2s	remaining: 13m 52s
3600:	learn: 0.5891479	test: 0.6199452	best: 0.6199447 (3599)	total: 3m 2s	remaining: 13m 51s
3610:	learn: 0.5890590	test: 0.6199379	best: 0.6199379 (3610)	total: 3m 3s	remaining: 13m 51s
3620:	learn: 0.5889543	test: 0.6199285	best: 0.6199281 (3619)	

...

16480:	learn: 0.4980635	test: 0.6164178	best: 0.6164178 (16480)	total: 13m 25s	remaining: 2m 51s
16490:	learn: 0.4979928	test: 0.6164135	best: 0.6164135 (16490)	total: 13m 25s	remaining: 2m 51s
16500:	learn: 0.4979248	test: 0.6164104	best: 0.6164104 (16500)	total: 13m 26s	remaining: 2m 50s
16510:	learn: 0.4978584	test: 0.6164091	best: 0.6164087 (16509)	total: 13m 26s	remaining: 2m 50s
16520:	learn: 0.4977968	test: 0.6164068	best: 0.6164054 (16517)	total: 13m 27s	remaining: 2m 50s
16530:	learn: 0.4977396	test: 0.6164055	best: 0.6164042 (16525)	total: 13m 28s	remaining: 2m 49s
16540:	learn: 0.4976723	test: 0.6164013	best: 0.6164000 (16536)	total: 13m 28s	remaining: 2m 49s
16550:	learn: 0.4976116	test: 0.6163984	best: 0.6163984 (16550)	total: 13m 29s	remaining: 2m 48s
16560:	learn: 0.4975556	test: 0.6163928	best: 0.6163926 (16559)	total: 13m 30s	remaining: 2m 48s
16570:	learn: 0.4974976	test: 0.6163930	best: 0.6163926 (16559)	total: 13m 30s	remaining: 2m 47s
16580:	learn: 0.4974383	test: 

17330:	learn: 0.4930720	test: 0.6163425	best: 0.6163356 (17232)	total: 14m 15s	remaining: 2m 11s
17340:	learn: 0.4930026	test: 0.6163442	best: 0.6163356 (17232)	total: 14m 15s	remaining: 2m 11s
17350:	learn: 0.4929237	test: 0.6163469	best: 0.6163356 (17232)	total: 14m 16s	remaining: 2m 10s
17360:	learn: 0.4928664	test: 0.6163506	best: 0.6163356 (17232)	total: 14m 16s	remaining: 2m 10s
17370:	learn: 0.4928001	test: 0.6163465	best: 0.6163356 (17232)	total: 14m 17s	remaining: 2m 9s
17380:	learn: 0.4927425	test: 0.6163407	best: 0.6163356 (17232)	total: 14m 18s	remaining: 2m 9s
17390:	learn: 0.4926886	test: 0.6163392	best: 0.6163356 (17232)	total: 14m 18s	remaining: 2m 8s
17400:	learn: 0.4926263	test: 0.6163392	best: 0.6163356 (17232)	total: 14m 19s	remaining: 2m 8s
17410:	learn: 0.4925720	test: 0.6163363	best: 0.6163356 (17232)	total: 14m 20s	remaining: 2m 7s
17420:	learn: 0.4925231	test: 0.6163350	best: 0.6163343 (17417)	total: 14m 20s	remaining: 2m 7s
17430:	learn: 0.4924703	test: 0.6163

18180:	learn: 0.4880683	test: 0.6163287	best: 0.6163144 (17985)	total: 14m 59s	remaining: 1m 29s
18190:	learn: 0.4880107	test: 0.6163229	best: 0.6163144 (17985)	total: 14m 59s	remaining: 1m 29s
18200:	learn: 0.4879526	test: 0.6163216	best: 0.6163144 (17985)	total: 14m 59s	remaining: 1m 28s
18210:	learn: 0.4878982	test: 0.6163193	best: 0.6163144 (17985)	total: 15m	remaining: 1m 28s
18220:	learn: 0.4878394	test: 0.6163223	best: 0.6163144 (17985)	total: 15m	remaining: 1m 27s
18230:	learn: 0.4877769	test: 0.6163227	best: 0.6163144 (17985)	total: 15m	remaining: 1m 27s
18240:	learn: 0.4877212	test: 0.6163234	best: 0.6163144 (17985)	total: 15m 1s	remaining: 1m 26s
18250:	learn: 0.4876559	test: 0.6163201	best: 0.6163144 (17985)	total: 15m 1s	remaining: 1m 26s
18260:	learn: 0.4875940	test: 0.6163177	best: 0.6163144 (17985)	total: 15m 1s	remaining: 1m 25s
18270:	learn: 0.4875376	test: 0.6163200	best: 0.6163144 (17985)	total: 15m 2s	remaining: 1m 25s
18280:	learn: 0.4874863	test: 0.6163173	best: 

19040:	learn: 0.4831788	test: 0.6163096	best: 0.6162931 (18746)	total: 15m 26s	remaining: 46.7s
19050:	learn: 0.4831174	test: 0.6163183	best: 0.6162931 (18746)	total: 15m 26s	remaining: 46.2s
19060:	learn: 0.4830717	test: 0.6163173	best: 0.6162931 (18746)	total: 15m 26s	remaining: 45.7s
19070:	learn: 0.4830270	test: 0.6163191	best: 0.6162931 (18746)	total: 15m 27s	remaining: 45.2s
19080:	learn: 0.4829780	test: 0.6163236	best: 0.6162931 (18746)	total: 15m 27s	remaining: 44.7s
19090:	learn: 0.4829235	test: 0.6163202	best: 0.6162931 (18746)	total: 15m 27s	remaining: 44.2s
19100:	learn: 0.4828720	test: 0.6163239	best: 0.6162931 (18746)	total: 15m 28s	remaining: 43.7s
19110:	learn: 0.4828266	test: 0.6163255	best: 0.6162931 (18746)	total: 15m 28s	remaining: 43.2s
19120:	learn: 0.4827633	test: 0.6163229	best: 0.6162931 (18746)	total: 15m 28s	remaining: 42.7s
19130:	learn: 0.4827023	test: 0.6163202	best: 0.6162931 (18746)	total: 15m 29s	remaining: 42.2s
19140:	learn: 0.4826498	test: 0.6163254	

19900:	learn: 0.4783568	test: 0.6163467	best: 0.6162931 (18746)	total: 15m 53s	remaining: 4.74s
19910:	learn: 0.4783045	test: 0.6163469	best: 0.6162931 (18746)	total: 15m 53s	remaining: 4.26s
19920:	learn: 0.4782488	test: 0.6163439	best: 0.6162931 (18746)	total: 15m 54s	remaining: 3.78s
19930:	learn: 0.4781892	test: 0.6163462	best: 0.6162931 (18746)	total: 15m 54s	remaining: 3.3s
19940:	learn: 0.4781331	test: 0.6163484	best: 0.6162931 (18746)	total: 15m 54s	remaining: 2.82s
19950:	learn: 0.4780802	test: 0.6163463	best: 0.6162931 (18746)	total: 15m 55s	remaining: 2.35s
19960:	learn: 0.4780348	test: 0.6163475	best: 0.6162931 (18746)	total: 15m 55s	remaining: 1.87s
19970:	learn: 0.4779851	test: 0.6163458	best: 0.6162931 (18746)	total: 15m 55s	remaining: 1.39s
19980:	learn: 0.4779332	test: 0.6163431	best: 0.6162931 (18746)	total: 15m 56s	remaining: 909ms
19990:	learn: 0.4778775	test: 0.6163452	best: 0.6162931 (18746)	total: 15m 56s	remaining: 431ms
19999:	learn: 0.4778198	test: 0.6163495	b

In [17]:
y_pred = model.predict(x_val)
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_val, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print('val auc: {}'.format(roc_auc))

val auc: 0.5687891794211761


In [18]:
from sklearn.ensemble import AdaBoostClassifier

boosting3 = AdaBoostClassifier(base_estimator=model, n_estimators=3, learning_rate=0.1)   
boosting3.fit(x_train, y_train)
print(boosting3.score(x_train, y_train))
print(boosting3.score(x_val, y_val))

0:	learn: 0.6931153	total: 18.9ms	remaining: 6m 17s
1:	learn: 0.6930965	total: 36.7ms	remaining: 6m 6s
2:	learn: 0.6930669	total: 53.7ms	remaining: 5m 57s
3:	learn: 0.6930364	total: 70.8ms	remaining: 5m 54s
4:	learn: 0.6930204	total: 98.9ms	remaining: 6m 35s
5:	learn: 0.6929898	total: 125ms	remaining: 6m 56s
6:	learn: 0.6929743	total: 154ms	remaining: 7m 18s
7:	learn: 0.6929585	total: 175ms	remaining: 7m 17s
8:	learn: 0.6929428	total: 203ms	remaining: 7m 30s
9:	learn: 0.6929272	total: 221ms	remaining: 7m 21s
10:	learn: 0.6929118	total: 243ms	remaining: 7m 20s
11:	learn: 0.6928962	total: 269ms	remaining: 7m 27s
12:	learn: 0.6928648	total: 285ms	remaining: 7m 18s
13:	learn: 0.6928499	total: 309ms	remaining: 7m 20s
14:	learn: 0.6928344	total: 335ms	remaining: 7m 26s
15:	learn: 0.6928185	total: 355ms	remaining: 7m 23s
16:	learn: 0.6928031	total: 383ms	remaining: 7m 29s
17:	learn: 0.6927875	total: 401ms	remaining: 7m 25s
18:	learn: 0.6927724	total: 416ms	remaining: 7m 17s
19:	learn: 0.69275

161:	learn: 0.6898895	total: 3.62s	remaining: 7m 23s
162:	learn: 0.6898742	total: 3.63s	remaining: 7m 22s
163:	learn: 0.6898598	total: 3.66s	remaining: 7m 23s
164:	learn: 0.6898445	total: 3.68s	remaining: 7m 22s
165:	learn: 0.6898151	total: 3.69s	remaining: 7m 21s
166:	learn: 0.6897861	total: 3.71s	remaining: 7m 20s
167:	learn: 0.6897716	total: 3.74s	remaining: 7m 21s
168:	learn: 0.6897571	total: 3.77s	remaining: 7m 21s
169:	learn: 0.6897276	total: 3.78s	remaining: 7m 21s
170:	learn: 0.6897127	total: 3.81s	remaining: 7m 21s
171:	learn: 0.6896835	total: 3.83s	remaining: 7m 21s
172:	learn: 0.6896688	total: 3.85s	remaining: 7m 21s
173:	learn: 0.6896539	total: 3.88s	remaining: 7m 21s
174:	learn: 0.6896393	total: 3.9s	remaining: 7m 21s
175:	learn: 0.6896108	total: 3.91s	remaining: 7m 20s
176:	learn: 0.6895952	total: 3.94s	remaining: 7m 21s
177:	learn: 0.6895807	total: 3.96s	remaining: 7m 21s
178:	learn: 0.6895658	total: 3.98s	remaining: 7m 21s
179:	learn: 0.6895509	total: 4.01s	remaining: 7

322:	learn: 0.6869846	total: 7.2s	remaining: 7m 18s
323:	learn: 0.6869711	total: 7.23s	remaining: 7m 18s
324:	learn: 0.6869564	total: 7.25s	remaining: 7m 19s
325:	learn: 0.6869429	total: 7.28s	remaining: 7m 19s
326:	learn: 0.6869288	total: 7.3s	remaining: 7m 19s
327:	learn: 0.6869148	total: 7.33s	remaining: 7m 19s
328:	learn: 0.6868867	total: 7.34s	remaining: 7m 19s
329:	learn: 0.6868725	total: 7.36s	remaining: 7m 18s
330:	learn: 0.6868586	total: 7.39s	remaining: 7m 19s
331:	learn: 0.6868443	total: 7.41s	remaining: 7m 18s
332:	learn: 0.6868307	total: 7.43s	remaining: 7m 19s
333:	learn: 0.6868164	total: 7.46s	remaining: 7m 19s
334:	learn: 0.6868025	total: 7.48s	remaining: 7m 19s
335:	learn: 0.6867748	total: 7.5s	remaining: 7m 18s
336:	learn: 0.6867605	total: 7.53s	remaining: 7m 19s
337:	learn: 0.6867469	total: 7.55s	remaining: 7m 19s
338:	learn: 0.6867327	total: 7.57s	remaining: 7m 19s
339:	learn: 0.6867186	total: 7.6s	remaining: 7m 19s
340:	learn: 0.6866913	total: 7.62s	remaining: 7m 1

481:	learn: 0.6841903	total: 10.8s	remaining: 7m 17s
482:	learn: 0.6841768	total: 10.8s	remaining: 7m 16s
483:	learn: 0.6841505	total: 10.8s	remaining: 7m 16s
484:	learn: 0.6841371	total: 10.9s	remaining: 7m 16s
485:	learn: 0.6841106	total: 10.9s	remaining: 7m 16s
486:	learn: 0.6840971	total: 10.9s	remaining: 7m 16s
487:	learn: 0.6840707	total: 10.9s	remaining: 7m 15s
488:	learn: 0.6840573	total: 10.9s	remaining: 7m 16s
489:	learn: 0.6840443	total: 10.9s	remaining: 7m 15s
490:	learn: 0.6840307	total: 11s	remaining: 7m 15s
491:	learn: 0.6840176	total: 11s	remaining: 7m 16s
492:	learn: 0.6840041	total: 11s	remaining: 7m 16s
493:	learn: 0.6839907	total: 11.1s	remaining: 7m 16s
494:	learn: 0.6839775	total: 11.1s	remaining: 7m 16s
495:	learn: 0.6839509	total: 11.1s	remaining: 7m 16s
496:	learn: 0.6839379	total: 11.1s	remaining: 7m 16s
497:	learn: 0.6839113	total: 11.2s	remaining: 7m 16s
498:	learn: 0.6838855	total: 11.2s	remaining: 7m 16s
499:	learn: 0.6838718	total: 11.2s	remaining: 7m 17s

642:	learn: 0.6814945	total: 14.4s	remaining: 7m 14s
643:	learn: 0.6814824	total: 14.4s	remaining: 7m 14s
644:	learn: 0.6814573	total: 14.5s	remaining: 7m 14s
645:	learn: 0.6814443	total: 14.5s	remaining: 7m 14s
646:	learn: 0.6814194	total: 14.5s	remaining: 7m 14s
647:	learn: 0.6813942	total: 14.5s	remaining: 7m 13s
648:	learn: 0.6813822	total: 14.6s	remaining: 7m 14s
649:	learn: 0.6813692	total: 14.6s	remaining: 7m 14s
650:	learn: 0.6813444	total: 14.6s	remaining: 7m 14s
651:	learn: 0.6813316	total: 14.6s	remaining: 7m 14s
652:	learn: 0.6813069	total: 14.7s	remaining: 7m 14s
653:	learn: 0.6812944	total: 14.7s	remaining: 7m 14s
654:	learn: 0.6812816	total: 14.7s	remaining: 7m 13s
655:	learn: 0.6812687	total: 14.7s	remaining: 7m 14s
656:	learn: 0.6812438	total: 14.7s	remaining: 7m 13s
657:	learn: 0.6812312	total: 14.8s	remaining: 7m 13s
658:	learn: 0.6812186	total: 14.8s	remaining: 7m 13s
659:	learn: 0.6812020	total: 14.8s	remaining: 7m 13s
660:	learn: 0.6811927	total: 14.8s	remaining: 

...

19405:	learn: 0.6901084	total: 13m 4s	remaining: 24s
19406:	learn: 0.6901082	total: 13m 4s	remaining: 24s
19407:	learn: 0.6901080	total: 13m 4s	remaining: 23.9s
19408:	learn: 0.6901080	total: 13m 4s	remaining: 23.9s
19409:	learn: 0.6901079	total: 13m 4s	remaining: 23.9s
19410:	learn: 0.6901080	total: 13m 5s	remaining: 23.8s
19411:	learn: 0.6901077	total: 13m 5s	remaining: 23.8s
19412:	learn: 0.6901077	total: 13m 5s	remaining: 23.7s
19413:	learn: 0.6901076	total: 13m 5s	remaining: 23.7s
19414:	learn: 0.6901073	total: 13m 5s	remaining: 23.7s
19415:	learn: 0.6901071	total: 13m 5s	remaining: 23.6s
19416:	learn: 0.6901071	total: 13m 5s	remaining: 23.6s
19417:	learn: 0.6901071	total: 13m 5s	remaining: 23.5s
19418:	learn: 0.6901069	total: 13m 5s	remaining: 23.5s
19419:	learn: 0.6901068	total: 13m 5s	remaining: 23.5s
19420:	learn: 0.6901065	total: 13m 5s	remaining: 23.4s
19421:	learn: 0.6901065	total: 13m 5s	remaining: 23.4s
19422:	learn: 0.6901063	total: 13m 5s	remaining: 23.3s
19423:	learn: 

19556:	learn: 0.6900913	total: 13m 12s	remaining: 17.9s
19557:	learn: 0.6900913	total: 13m 12s	remaining: 17.9s
19558:	learn: 0.6900911	total: 13m 12s	remaining: 17.9s
19559:	learn: 0.6900911	total: 13m 12s	remaining: 17.8s
19560:	learn: 0.6900910	total: 13m 12s	remaining: 17.8s
19561:	learn: 0.6900908	total: 13m 12s	remaining: 17.7s
19562:	learn: 0.6900907	total: 13m 12s	remaining: 17.7s
19563:	learn: 0.6900907	total: 13m 12s	remaining: 17.7s
19564:	learn: 0.6900907	total: 13m 12s	remaining: 17.6s
19565:	learn: 0.6900906	total: 13m 12s	remaining: 17.6s
19566:	learn: 0.6900906	total: 13m 12s	remaining: 17.5s
19567:	learn: 0.6900902	total: 13m 12s	remaining: 17.5s
19568:	learn: 0.6900903	total: 13m 13s	remaining: 17.5s
19569:	learn: 0.6900902	total: 13m 13s	remaining: 17.4s
19570:	learn: 0.6900901	total: 13m 13s	remaining: 17.4s
19571:	learn: 0.6900899	total: 13m 13s	remaining: 17.3s
19572:	learn: 0.6900899	total: 13m 13s	remaining: 17.3s
19573:	learn: 0.6900896	total: 13m 13s	remaining

19704:	learn: 0.6900740	total: 13m 19s	remaining: 12s
19705:	learn: 0.6900740	total: 13m 19s	remaining: 11.9s
19706:	learn: 0.6900740	total: 13m 19s	remaining: 11.9s
19707:	learn: 0.6900740	total: 13m 19s	remaining: 11.8s
19708:	learn: 0.6900739	total: 13m 19s	remaining: 11.8s
19709:	learn: 0.6900737	total: 13m 19s	remaining: 11.8s
19710:	learn: 0.6900737	total: 13m 19s	remaining: 11.7s
19711:	learn: 0.6900734	total: 13m 20s	remaining: 11.7s
19712:	learn: 0.6900735	total: 13m 20s	remaining: 11.6s
19713:	learn: 0.6900734	total: 13m 20s	remaining: 11.6s
19714:	learn: 0.6900733	total: 13m 20s	remaining: 11.6s
19715:	learn: 0.6900731	total: 13m 20s	remaining: 11.5s
19716:	learn: 0.6900730	total: 13m 20s	remaining: 11.5s
19717:	learn: 0.6900728	total: 13m 20s	remaining: 11.4s
19718:	learn: 0.6900727	total: 13m 20s	remaining: 11.4s
19719:	learn: 0.6900725	total: 13m 20s	remaining: 11.4s
19720:	learn: 0.6900725	total: 13m 20s	remaining: 11.3s
19721:	learn: 0.6900722	total: 13m 20s	remaining: 

19851:	learn: 0.6900576	total: 13m 26s	remaining: 6.01s
19852:	learn: 0.6900573	total: 13m 26s	remaining: 5.97s
19853:	learn: 0.6900572	total: 13m 26s	remaining: 5.93s
19854:	learn: 0.6900569	total: 13m 26s	remaining: 5.89s
19855:	learn: 0.6900569	total: 13m 26s	remaining: 5.85s
19856:	learn: 0.6900569	total: 13m 26s	remaining: 5.81s
19857:	learn: 0.6900563	total: 13m 26s	remaining: 5.77s
19858:	learn: 0.6900563	total: 13m 26s	remaining: 5.73s
19859:	learn: 0.6900560	total: 13m 26s	remaining: 5.69s
19860:	learn: 0.6900560	total: 13m 26s	remaining: 5.65s
19861:	learn: 0.6900560	total: 13m 26s	remaining: 5.61s
19862:	learn: 0.6900558	total: 13m 27s	remaining: 5.57s
19863:	learn: 0.6900557	total: 13m 27s	remaining: 5.53s
19864:	learn: 0.6900557	total: 13m 27s	remaining: 5.49s
19865:	learn: 0.6900556	total: 13m 27s	remaining: 5.44s
19866:	learn: 0.6900554	total: 13m 27s	remaining: 5.4s
19867:	learn: 0.6900551	total: 13m 27s	remaining: 5.36s
19868:	learn: 0.6900549	total: 13m 27s	remaining:

0.6523810729599244
0.6513386677470543


In [19]:
y_pred = boosting3.predict(x_val)
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_val, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print('val auc: {}'.format(roc_auc))

val auc: 0.5489955600119532


In [20]:
df_test['Predicted'] = boosting3.predict_proba(x_test)[:,1]
df_test[["id","Predicted"]].to_csv('submission_cat_1.csv')